# QC Handbook 
## Diamond 2:
### Implementations:
- QC on the preprocessed data
	- Check carpet plots for preprocessed subjects
	- Were the 1stlevels run for all tasks
	- What contrasts/PPI were run

### QC Implementations to figure out which subjects should be removed
- Get motion pars for each subject (6 motion 1 FD)
    - calculate min/max/avg
    - Use specific exclusion value for each par
        - Which tasks have unasable motion?
        - What value did it have?
- Run percent coverage script
    - If value is below certain percent threshold, output that ROI
    - If vital areas have dropout, exclude that task
    - What areas are most vital?
- Check to make sure time series was completely collected for task
    - How many timepoints should there be for the task?
        - If it has less than the required timepoints, output the error and exlude that task
|

## QC on the RAWDATA
- Time Series correct length
- Serious motion check
    - Alex/Tyler could build a tool to look at this effectively
        - The tool should be able to be used by the data manager
- Serious dropout check
- Was Physio data collected
- Are the behavioral files present/complete for all tasks

In [20]:
import sys
sys.path.insert(1, 'jupyter-notebooks')
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import glob
import os
from pandasql import sqldf
pysqldf = lambda q: sqldf(q, globals())

In [55]:
#query = "SELECT subject_name,series_id,protocol_name, dim4 FROM df WHERE protocol_name = 'resting-state' AND (dim4 <> 960)"
### OUTPUT ROWS OF DATABASE WHERE PROTOCOL_NAME IS NOT OF THE CORRECT TIME SERIES LENGTH ###
query = " SELECT subject_name, protocol_name, dim4 FROM df WHERE (protocol_name ='reward_2' AND (dim4 <> 990 AND dim4 <> 3)) OR (protocol_name ='reward_1' AND (dim4 <> 990 AND dim4 <> 3)) OR (protocol_name ='EFNback_1' AND (dim4 <> 840 AND dim4 <> 3)) OR (protocol_name ='EFNback_2' AND (dim4 <> 840 AND dim4 <> 3)) OR (protocol_name ='resting-state' AND (dim4 <> 960 AND dim4 <> 3)) OR (protocol_name ='dynamic faces' AND (dim4 <> 1512 AND dim4 <> 3))"
#query = " SELECT subject_name, protocol_name, dim4 FROM df WHERE protocol_name = 'EFNback_2'"

In [56]:
results_df = pd.DataFrame()
for x in files:
    df = pd.read_csv(x, sep='\t')
    df['subject_name'] = os.path.basename(x).split('_')[0]
    #extract rows where protocol is 'restingstate' and the dim4 is not 960
    ###query = "SELECT subject_name,series_id,protocol_name, dim4 FROM df WHERE protocol_name = 'resting-state' AND (dim4 <> 960)"
    current_results = pysqldf(query)
    results_df = results_df.append(current_results)

In [57]:
results_df.set_index('subject_name').sort_index()

protocol_name dim4
subject_name                    
50004         resting-state  900
50052              reward_2  257
50081         resting-state  156
50153              reward_1  117
50158         resting-state   36
50204              reward_1   27

## The QC_Pipeline module functionality
### The QC_Pipeline module can generate the following information:
- `task_df`: (DataFrame) Table containing mean/max metrics for 6 motion_pars and Framewise_displacement
- `mean_table`: (DataFrame) Table containing only values that have been flagged with mean value > `0.5`
- `max_table`: (DataFrame) Table containing only values that have been flagged with max value > `5`
- `mean_table_highlighted`: (StyleFrame) Table containing same values as `mean_table` but with the flagged values highlighted
- `max_table_highlighted`: (StyleFrame) Table containing same values as `max_table` but with the flagged values highlighted
- `mean_exclued`: (Integer) Number of subjects that were flagged for the mean
- `max_excluded`: (Integer) Number of subjects that were flagged for the max
- `percent_coverage_table`: (DataFrame) Table containing the percent coverage found for each ROI present in the specified atlas
- `percent_coverage_highlighted`: (StyleFrame) Same table as `percent_coverage_table` but with ROIs where subject has less than 20% coverage highlighted

## Example 1: Compare variables for 'reward1' and 'reward2' tasks for NON subjects

In [40]:
from QC_Pipeline import Task_DataFrame as QC #Import custom module for QC
reward1_NON = QC('reward1', 'Preprocessed/NON') #specify task and folder of fmriprep data
reward2_NON = QC('reward2', 'Preprocessed/NON')

reward1 and Preprocessed/NON
reward2 and Preprocessed/NON


In [41]:
#display the generated tables
#print('task_df')
#display(reward1_NON.task_df.sort_index()) #Jupyter function to display a DataFrame/StyleFrame
print('mean_table')
display(reward1_NON.mean_table.sort_index())
display(reward2_NON.mean_table.sort_index())
print('max_table')
display(reward1_NON.max_table.sort_index())
display(reward2_NON.max_table.sort_index())
print('mean_table_highlighted')
display(reward1_NON.mean_table_highlighted)
display(reward2_NON.mean_table_highlighted)
print('max_table_highlighted')
display(reward1_NON.max_table_highlighted)
display(reward2_NON.max_table_highlighted)
print(f'mean_excluded for {reward1_NON.task} is {reward1_NON.mean_excluded}')
print(f'mean_excluded for {reward2_NON.task} is {reward2_NON.mean_excluded}')
print(f'max_excluded for {reward1_NON.task} is {reward1_NON.max_excluded}')
print(f'max_excluded for {reward2_NON.task} is {reward2_NON.max_excluded}')

mean_table


trans_x_mean  trans_x_max  trans_y_mean  trans_y_max  trans_z_mean  \
sub-50004      0.222023     1.750950      0.553476     1.946310      3.241417   
sub-50007     -0.254381     0.261767      0.813579     1.462400      1.537667   
sub-50010      0.053676     0.337900     -0.000585     1.900300     -0.637176   
sub-50018     -0.101026     0.170036      0.312363     2.244070      0.629616   
sub-50054      0.361027     2.838840      1.682646     4.664190      1.684133   
sub-50078     -0.193492     0.232719      0.502084     4.466080      0.447689   
sub-50097     -0.013158     0.067910      0.061058     0.497946     -0.181071   
sub-50108     -0.215702     0.479461     -0.048120     1.784200     -0.519160   
sub-50111      0.667860     2.374430      0.643220     3.206360      0.330531   
sub-50122      0.883504     2.598230     -0.471854     2.968290      0.741319   
sub-50126     -0.004877     0.352801     -0.032829     0.445494      0.272311   
sub-50183      0.003328     1.875110     -0.072608     0.396009      0.298760   
sub-50187      0.050514     0.502770      0.100200     0.309199      0.115258   
sub-50581      0.180713     0.745580     -0.038235     0.919633      0.502392   

           trans_z_max  rot_x_mean  rot_x_max  rot_y_mean  rot_y_max  \
sub-50004     8.624440    0.025200   0.167000   -0.004717   0.009370   
sub-50007     2.732340    0.033033   0.071914    0.027483   0.037505   
sub-50010     0.833675   -0.001603   0.162232    0.005119   0.020008   
sub-50018     3.857400    0.003998   0.044760   -0.000406   0.002021   
sub-50054     5.653390    0.050024   0.154200   -0.004981   0.044156   
sub-50078     5.030890    0.008756   0.102476   -0.001239   0.033751   
sub-50097     0.296285   -0.003762   0.055113    0.003800   0.008692   
sub-50108     4.444020    0.003726   0.122884    0.005113   0.029365   
sub-50111     3.548280    0.026256   0.140114   -0.016149   0.013647   
sub-50122     3.116280   -0.053747   0.136651   -0.008582   0.018767   
sub-50126     1.762300   -0.008839   0.052727    0.003552   0.011111   
sub-50183     1.516680   -0.007624   0.044860    0.001891   0.012287   
sub-50187     0.781285   -0.000084   0.008636   -0.001688   0.000157   
sub-50581     2.623210   -0.025598  -0.004792   -0.000591   0.002138   

           rot_z_mean  rot_z_max  framewise_displacement_mean  \
sub-50004    0.001332   0.024556                     0.814907   
sub-50007    0.016878   0.024860                     0.336604   
sub-50010    0.001855   0.011895                     0.517233   
sub-50018   -0.001491   0.000521                     0.167692   
sub-50054    0.009188   0.077487                     1.399908   
sub-50078    0.004217   0.024156                     0.548282   
sub-50097   -0.003225   0.001555                     0.222917   
sub-50108   -0.003252   0.008536                     0.617658   
sub-50111   -0.030805   0.002228                     0.553755   
sub-50122    0.012838   0.031198                     0.628040   
sub-50126    0.001637   0.012637                     0.462366   
sub-50183   -0.007642   0.025520                     0.528052   
sub-50187    0.000394   0.003460                     0.116132   
sub-50581    0.002220   0.005746                     0.200404   

           framewise_displacement_max  
sub-50004                   10.648861  
sub-50007                    5.243716  
sub-50010                    6.557016  
sub-50018                    5.568360  
sub-50054                   10.786654  
sub-50078                   13.276715  
sub-50097                    6.398876  
sub-50108                   19.250010  
sub-50111                   23.302613  
sub-50122                   13.513218  
sub-50126                    5.889322  
sub-50183                   11.464627  
sub-50187                    6.745683  
sub-50581                    5.936480

trans_x_mean  trans_x_max  trans_y_mean  trans_y_max  trans_z_mean  \
sub-50004     -0.080278     1.500810     -0.150431     5.302210      1.404223   
sub-50007     -0.255059     0.553391      1.252402     9.992270      2.444278   
sub-50009      0.202353     1.356410      0.435823     1.064690      0.663347   
sub-50014     -0.000209     0.324646     -0.855255     0.001236     -3.129802   
sub-50054     -1.063421     0.572521      1.266027     3.584790      3.280941   
sub-50078      0.080281     0.292096     -0.171176     2.816530     -0.007470   
sub-50081      0.579115     2.936740      1.043766     3.888810      2.461317   
sub-50101     -0.385750     0.008609     -0.710838     0.619748     -0.950701   
sub-50108      0.580560     1.048810      0.343009     1.688320      1.240451   
sub-50111      0.005696     8.518200      1.102481    13.173500      5.383036   
sub-50119      0.217237     0.488446     -0.219892     0.439973     -0.049510   
sub-50122     -0.285219     0.200998     -0.272515     1.178790     -2.176682   
sub-50126      0.278212     1.078720      0.021753     1.421620      0.794547   
sub-50167     -0.065431     0.044954      0.433096     1.585070      0.439536   
sub-50183     -0.152163     0.876849      0.637154     1.371030      1.213217   
sub-50187     -0.025272     0.715834      0.348194     1.261470      0.575742   

           trans_z_max  rot_x_mean  rot_x_max  rot_y_mean  rot_y_max  \
sub-50004     7.377170   -0.006577   0.068773   -0.000432   0.015299   
sub-50007    10.813200    0.032785   0.327762    0.004601   0.029849   
sub-50009     5.049590    0.014254   0.070359   -0.004077   0.001983   
sub-50014     0.246056   -0.031714   0.000982   -0.012146   0.000724   
sub-50054     6.353830    0.023290   0.111776    0.026363   0.140252   
sub-50078     4.502570   -0.018820   0.057336   -0.008172   0.004045   
sub-50081    10.592700    0.017459   0.063888   -0.001820   0.010314   
sub-50101     2.325930   -0.040990   0.001509    0.016670   0.030446   
sub-50108     3.187610   -0.017659   0.076063   -0.024740  -0.000000   
sub-50111    25.245200    0.003828   0.301927   -0.015963   0.043005   
sub-50119     1.164230   -0.018816   0.001116   -0.007724  -0.000433   
sub-50122     0.213580    0.014732   0.148160   -0.004901   0.017349   
sub-50126     3.879630   -0.004650   0.041859   -0.003838   0.003844   
sub-50167     1.405480    0.014606   0.104298    0.005143   0.022594   
sub-50183     2.960950    0.032645   0.053501   -0.001310   0.002672   
sub-50187     2.811700    0.005209   0.022396    0.002818   0.055262   

           rot_z_mean  rot_z_max  framewise_displacement_mean  \
sub-50004   -0.001312   0.037061                     1.075785   
sub-50007    0.005692   0.066835                     0.876180   
sub-50009   -0.000427   0.004248                     0.371215   
sub-50014    0.018643   0.043581                     0.233580   
sub-50054   -0.014822   0.033164                     1.535651   
sub-50078    0.008360   0.018608                     0.477705   
sub-50081    0.005205   0.043600                     0.698317   
sub-50101   -0.001666   0.011845                     0.337773   
sub-50108    0.014666   0.027866                     0.601332   
sub-50111    0.025465   0.158750                     1.492065   
sub-50119    0.002302   0.008020                     0.356778   
sub-50122   -0.000946   0.005088                     0.388786   
sub-50126    0.004933   0.023004                     0.446105   
sub-50167   -0.002338   0.002415                     0.247733   
sub-50183    0.006881   0.016648                     0.208536   
sub-50187    0.004394   0.019883                     0.349116   

           framewise_displacement_max  
sub-50004                   18.283774  
sub-50007                   18.737635  
sub-50009                    8.103745  
sub-50014                    9.336953  
sub-50054                   13.317419  
sub-50078                    7.391158  
sub-50081             

max_table


trans_x_mean  trans_x_max  trans_y_mean  trans_y_max  trans_z_mean  \
sub-50004      0.222023     1.750950      0.553476     1.946310      3.241417   
sub-50007     -0.254381     0.261767      0.813579     1.462400      1.537667   
sub-50010      0.053676     0.337900     -0.000585     1.900300     -0.637176   
sub-50018     -0.101026     0.170036      0.312363     2.244070      0.629616   
sub-50054      0.361027     2.838840      1.682646     4.664190      1.684133   
sub-50078     -0.193492     0.232719      0.502084     4.466080      0.447689   
sub-50080      0.055097     0.257079      0.164242     0.506012      0.877147   
sub-50108     -0.215702     0.479461     -0.048120     1.784200     -0.519160   
sub-50111      0.667860     2.374430      0.643220     3.206360      0.330531   
sub-50116     -0.051021     0.019497      0.123956     0.266611      0.687743   
sub-50117     -0.019930     0.044769      0.475077     1.408070      1.498387   
sub-50122      0.883504     2.598230     -0.471854     2.968290      0.741319   
sub-50127      0.009443     0.040108      0.628952     1.059940      0.687071   
sub-50141     -0.053405     0.225558      0.609695     0.870830     -0.205006   
sub-50149      0.033471     0.447768      0.155493     0.589047      1.089062   
sub-50153      0.043496     0.140333      0.545843     1.488680      0.366491   
sub-50167      0.077115     0.198763      0.474811     0.578652      0.753786   
sub-50175      0.035893     0.076074      0.174620     0.242940      0.533865   
sub-50179     -0.018229     0.126926      0.157121     0.346283      0.976513   
sub-50183      0.003328     1.875110     -0.072608     0.396009      0.298760   
sub-50581      0.180713     0.745580     -0.038235     0.919633      0.502392   

           trans_z_max  rot_x_mean  rot_x_max  rot_y_mean  rot_y_max  \
sub-50004     8.624440    0.025200   0.167000   -0.004717   0.009370   
sub-50007     2.732340    0.033033   0.071914    0.027483   0.037505   
sub-50010     0.833675   -0.001603   0.162232    0.005119   0.020008   
sub-50018     3.857400    0.003998   0.044760   -0.000406   0.002021   
sub-50054     5.653390    0.050024   0.154200   -0.004981   0.044156   
sub-50078     5.030890    0.008756   0.102476   -0.001239   0.033751   
sub-50080     1.914950   -0.006492   0.005031   -0.002651   0.004564   
sub-50108     4.444020    0.003726   0.122884    0.005113   0.029365   
sub-50111     3.548280    0.026256   0.140114   -0.016149   0.013647   
sub-50116     1.155700   -0.007728  -0.000628    0.000694   0.001728   
sub-50117     2.347430    0.002019   0.037845    0.005793   0.015810   
sub-50122     3.116280   -0.053747   0.136651   -0.008582   0.018767   
sub-50127     1.217400    0.010650   0.021555    0.002141   0.004206   
sub-50141     1.086190    0.032320   0.051755    0.008171   0.014737   
sub-50149     2.050320   -0.004744   0.007004   -0.002356   0.002345   
sub-50153     0.704392    0.016445   0.083572   -0.000914   0.001439   
sub-50167     0.951317   -0.023684  -0.004988   -0.002136   0.004101   
sub-50175     0.811319   -0.003513  -0.000742   -0.000392   0.002296   
sub-50179     4.172790   -0.002996   0.013366   -0.000154   0.004635   
sub-50183     1.516680   -0.007624   0.044860    0.001891   0.012287   
sub-50581     2.623210   -0.025598  -0.004792   -0.000591   0.002138   

           rot_z_mean  rot_z_max  framewise_displacement_mean  \
sub-50004    0.001332   0.024556                     0.814907   
sub-50007    0.016878   0.024860                     0.336604   
sub-50010    0.001855   0.011895                     0.517233   
sub-50018   -0.001491   0.000521                     0.167692   
sub-50054    0.009188   0.077487                     1.399908   
sub-50078    0.004217   0.024156                     0.548282   
sub-50080    0.003313   0.008491                     0.233673   
sub-50108   -0.003252   0.008536                     0.617658   
sub-50111   -0.030805   0.002228                     0.553

trans_x_mean  trans_x_max  trans_y_mean  trans_y_max  trans_z_mean  \
sub-50004     -0.080278     1.500810     -0.150431     5.302210      1.404223   
sub-50007     -0.255059     0.553391      1.252402     9.992270      2.444278   
sub-50009      0.202353     1.356410      0.435823     1.064690      0.663347   
sub-50010      0.051826     0.261793     -0.521869     0.483441     -1.047487   
sub-50052      0.007977     0.069885      0.655552     0.899394      1.027081   
sub-50054     -1.063421     0.572521      1.266027     3.584790      3.280941   
sub-50058      0.000560     0.150702      0.144091     0.509807      0.626572   
sub-50081      0.579115     2.936740      1.043766     3.888810      2.461317   
sub-50083     -0.039208    -0.005106      0.359274     0.755100      0.567711   
sub-50108      0.580560     1.048810      0.343009     1.688320      1.240451   
sub-50111      0.005696     8.518200      1.102481    13.173500      5.383036   
sub-50114      0.037779     0.133292      0.312382     0.710394      0.899013   
sub-50121      0.361354     0.961453      0.560138     0.912524      0.784177   
sub-50126      0.278212     1.078720      0.021753     1.421620      0.794547   
sub-50127     -0.106450    -0.008129      0.906460     1.602690      1.041514   
sub-50130      0.141370     0.261962      0.350446     0.624656      0.511017   
sub-50141     -0.166206     0.063086      0.099293     0.251691      1.939642   
sub-50149      0.046134     0.331683      0.651382     1.200430      2.686190   
sub-50171      0.148633     0.296046      0.556993     1.066960      0.539189   
sub-50174      0.053526     0.172737      0.108647     0.379810      0.539544   
sub-50179     -0.239448    -0.041546      0.159611     0.311152      1.198809   
sub-50183     -0.152163     0.876849      0.637154     1.371030      1.213217   
sub-50187     -0.025272     0.715834      0.348194     1.261470      0.575742   
sub-50581      0.156306     0.212580      0.101255     0.216679      0.596504   

           trans_z_max  rot_x_mean  rot_x_max  rot_y_mean  rot_y_max  \
sub-50004     7.377170   -0.006577   0.068773   -0.000432   0.015299   
sub-50007    10.813200    0.032785   0.327762    0.004601   0.029849   
sub-50009     5.049590    0.014254   0.070359   -0.004077   0.001983   
sub-50010     1.262450   -0.020475   0.031575    0.000435   0.005983   
sub-50052     1.628630    0.004162   0.011777    0.002853   0.006975   
sub-50054     6.353830    0.023290   0.111776    0.026363   0.140252   
sub-50058     2.670380    0.001960   0.012197   -0.000897   0.004178   
sub-50081    10.592700    0.017459   0.063888   -0.001820   0.010314   
sub-50083     1.295550    0.005308   0.015792   -0.003212   0.000063   
sub-50108     3.187610   -0.017659   0.076063   -0.024740  -0.000000   
sub-50111    25.245200    0.003828   0.301927   -0.015963   0.043005   
sub-50114     1.599910   -0.003972   0.012774   -0.002221   0.001831   
sub-50121     1.200470    0.004210   0.016473   -0.008982   0.002936   
sub-50126     3.879630   -0.004650   0.041859   -0.003838   0.003844   
sub-50127     1.674150    0.026914   0.052261    0.009223   0.022153   
sub-50130     1.523700    0.002938   0.018470   -0.000439   0.002164   
sub-50141     2.986290    0.006970   0.021786    0.003251   0.009229   
sub-50149     4.076210   -0.021502   0.014886    0.001083   0.003380   
sub-50171     1.237900    0.010233   0.031530   -0.007469  -0.000000   
sub-50174     1.181190   -0.006288   0.001150   -0.002841   0.000831   
sub-50179     3.550950   -0.004953   0.002126   -0.001313   0.003648   
sub-50183     2.960950    0.032645   0.053501   -0.001310   0.002672   
sub-50187     2.811700    0.005209   0.022396    0.002818   0.055262   
sub-50581     0.794171   -0.006146   0.001560    0.000301   0.002587   

           rot_z_mean  rot_z_max  framewise_displacement_mean  \
sub-50004   -0.001312   0.037061                     1.075785   
sub-50007    0.005692   0.066835                     0

mean_table_highlighted


max_table_highlighted


mean_excluded for reward1 is 14
mean_excluded for reward2 is 16
max_excluded for reward1 is 21
max_excluded for reward2 is 24


Example 2: Run percent coverage for reward1 NON subjects
- NOTE! This will take several minutes to run

In [42]:
#Use the dataframe we already generated and run the percent coverage script
reward1_NON.percent_coverage('percent_coverage/bnatlas.nii.gz', 'percent_coverage/bnatlas.nii.txt') #Specify the atlas and the labels to use

Preprocessed/NON
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/NON/sub-50002/ses-1/func/sub-50002_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50004/ses-1/func/sub-50004_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50006/ses-1/func/sub-50006_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50007/ses-1/func/sub-50007_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50008/ses-1/func/sub-50008_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50009/ses-1/func/sub-50009_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50010/ses-1/func/sub-50010_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50012/ses-1/func/sub-5

/data/D2/data/jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/data/D2/data/jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/data/D2/data/jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/data/D2/data/jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/data/D2/data/jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/data/D2/data/jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels


In [43]:
display(reward1_NON.percent_coverage_table) #Show the table that was generated

1 SFG_L_7_1  2 SFG_R_7_1  3 SFG_L_7_2  4 SFG_R_7_2  5 SFG_L_7_3  \
bnatlas.n     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50002     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50004     1.000000     1.000000     0.954139     1.000000     0.291123   
sub-50006     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50007     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50008     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50009     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50010     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50012     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50013     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50014     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50015     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50018     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50019     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50021     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50023     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50024     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50026     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50027     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50030     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50032     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50033     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50036     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50037     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50039     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50040     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50041     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50047     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50050     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50051     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50052     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50054     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50055     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50056     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50057     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50058     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50060     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50061     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50063     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50070     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50071     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50078     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50079     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50080     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50081     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50083     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50084     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50086     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50087     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50088     1.000000     1.000000     1.000000     1.000000     1.000000   
sub-50091     1.000000     1.0000

In [44]:
reward1_NON.output_low_coverage(0.5) #highlight cells which have output less than 50%

## QC on Pre-processed tasks
- create a list containing all of the task names for your BIDs formatted fmriprep data
- Specify the folders containing the subjects
- generate tables for each dataset and task
- output number subjects flagged for mean and max values

In [10]:
from QC_Pipeline import Task_DataFrame as QC #Import custom module for QC
tasks = ['reward1', 'reward2', 'efnback1', 'efnback2', 'dynface', 'rest']
subject_folders = ['Preprocessed/NON', 'Preprocessed/BPD']

QC_objects = [] #List which we will append the QC objects we create into.  This will allow for indexing later on
coverage_objects = [] #List to store percent coverage table outputs
for folder in subject_folders: #Loop thru Directories containing fmriprep data
    for task in tasks: #Loop thru each task
        task_object = QC(task, folder)
        QC_objects.append(task_object) #Output the new QC object to our list
        percent_coverage_table = task_object.percent_coverage('percent_coverage/bnatlas.nii.gz', 'percent_coverage/bnatlas.nii.txt')
        coverage_objects.append(percent_coverage_table)


reward1 and Preprocessed/NON
Preprocessed/NON
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/NON/sub-50002/ses-1/func/sub-50002_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50004/ses-1/func/sub-50004_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50006/ses-1/func/sub-50006_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50007/ses-1/func/sub-50007_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50008/ses-1/func/sub-50008_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50009/ses-1/func/sub-50009_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50010/ses-1/func/sub-50010_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/N

jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels


reward2 and Preprocessed/NON
Preprocessed/NON
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/NON/sub-50002/ses-1/func/sub-50002_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50004/ses-1/func/sub-50004_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50006/ses-1/func/sub-50006_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50007/ses-1/func/sub-50007_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50008/ses-1/func/sub-50008_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50009/ses-1/func/sub-50009_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50010/ses-1/func/sub-50010_ses-1_task-reward2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/N

jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels


efnback1 and Preprocessed/NON
Preprocessed/NON
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/NON/sub-50002/ses-1/func/sub-50002_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50004/ses-1/func/sub-50004_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50006/ses-1/func/sub-50006_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50007/ses-1/func/sub-50007_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50008/ses-1/func/sub-50008_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50009/ses-1/func/sub-50009_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/NON/sub-50010/ses-1/func/sub-50010_ses-1_task-efnback1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Prepro

...

efnback2 and Preprocessed/BPD
Preprocessed/BPD
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/BPD/sub-50003/ses-1/func/sub-50003_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50017/ses-1/func/sub-50017_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50025/ses-1/func/sub-50025_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50028/ses-1/func/sub-50028_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50044/ses-1/func/sub-50044_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50048/ses-1/func/sub-50048_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50062/ses-1/func/sub-50062_ses-1_task-efnback2_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Prepro

jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels


dynface and Preprocessed/BPD
Preprocessed/BPD
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/BPD/sub-50003/ses-1/func/sub-50003_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50017/ses-1/func/sub-50017_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50025/ses-1/func/sub-50025_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50028/ses-1/func/sub-50028_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50044/ses-1/func/sub-50044_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50048/ses-1/func/sub-50048_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50062/ses-1/func/sub-50062_ses-1_task-dynface_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/B

jupyter-notebooks/QC_Pipeline.py:191: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels


rest and Preprocessed/BPD
Preprocessed/BPD
['percent_coverage/bnatlas.nii.gz', 'Preprocessed/BPD/sub-50003/ses-1/func/sub-50003_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50017/ses-1/func/sub-50017_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50025/ses-1/func/sub-50025_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50028/ses-1/func/sub-50028_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50044/ses-1/func/sub-50044_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50048/ses-1/func/sub-50048_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50062/ses-1/func/sub-50062_ses-1_task-rest_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', 'Preprocessed/BPD/sub-50077/ses-1/func/

## Example 3:
### create a dictionary with each subject and what tasks did not meet the criteria

In [67]:
mean_dict = {}
max_dict = {}
for i, task in enumerate(tasks):
    for index, row in QC_objects[i].mean_table.iterrows(): #check thru each row of mean table. Add in task name to each sub key
        try:
            mean_dict[index].append(QC_objects[i].task) #try to append to a list of the subject
        except KeyError: #if the subject doesn't already have a key, create a key that is a list
            mean_dict[index] = [QC_objects[i].task]
    for index, row in QC_objects[i].max_table.iterrows(): #do the same thing for the max tables
        try:
            max_dict[index].append(QC_objects[i].task)
        except KeyError:
            max_dict[index] = [QC_objects[i].task]
            
for j, task in enumerate(tasks): # do the same thing for the BPD folders which are 6 indeces away
    i = j+6
    for index, row in QC_objects[i].mean_table.iterrows(): #check thru each row of mean table. Add in task name to each sub key
        try:
            mean_dict[index].append(QC_objects[i].task) #try to append to a list of the subject
        except KeyError: #if the subject doesn't already have a key, create a key that is a list
            mean_dict[index] = [QC_objects[i].task]
    for index, row in QC_objects[i].max_table.iterrows(): #do the same thing for the max tables
        try:
            max_dict[index].append(QC_objects[i].task)
        except KeyError:
            max_dict[index] = [QC_objects[i].task]

In [72]:
mean_dict #subject tasks that had an average motion parameter less than 0.5

{'sub-50108': ['reward1',
  'reward2',
  'efnback1',
  'efnback2',
  'dynface',
  'rest'],
 'sub-50054': ['reward1',
  'reward2',
  'efnback1',
  'efnback2',
  'dynface',
  'rest'],
 'sub-50007': ['reward1', 'reward2', 'efnback2', 'dynface', 'rest'],
 'sub-50010': ['reward1'],
 'sub-50078': ['reward1', 'reward2', 'efnback1', 'efnback2', 'rest'],
 'sub-50126': ['reward1', 'reward2'],
 'sub-50183': ['reward1', 'reward2', 'efnback1', 'efnback2', 'dynface'],
 'sub-50111': ['reward1', 'reward2', 'efnback1', 'efnback2'],
 'sub-50018': ['reward1', 'efnback2', 'dynface'],
 'sub-50122': ['reward1', 'reward2', 'efnback1', 'dynface', 'rest'],
 'sub-50581': ['reward1'],
 'sub-50187': ['reward1', 'reward2'],
 'sub-50097': ['reward1'],
 'sub-50004': ['reward1',
  'reward2',
  'efnback1',
  'efnback2',
  'dynface',
  'rest'],
 'sub-50101': ['reward2'],
 'sub-50014': ['reward2'],
 'sub-50119': ['reward2', 'efnback2'],
 'sub-50009': ['reward2', 'dynface', 'rest'],
 'sub-50167': ['reward2'],
 'sub-50081

In [74]:
max_dict #subject tasks that had a max motion parameter less than 5

{'sub-50116': ['reward1', 'rest'],
 'sub-50149': ['reward1', 'reward2', 'efnback2', 'dynface', 'rest'],
 'sub-50141': ['reward1', 'reward2', 'efnback1', 'dynface'],
 'sub-50108': ['reward1',
  'reward2',
  'efnback1',
  'efnback2',
  'dynface',
  'rest'],
 'sub-50054': ['reward1',
  'reward2',
  'efnback1',
  'efnback2',
  'dynface',
  'rest'],
 'sub-50175': ['reward1', 'efnback1', 'dynface'],
 'sub-50007': ['reward1', 'reward2', 'dynface', 'rest'],
 'sub-50010': ['reward1', 'reward2'],
 'sub-50078': ['reward1', 'efnback1', 'efnback2'],
 'sub-50179': ['reward1', 'reward2'],
 'sub-50153': ['reward1', 'efnback1'],
 'sub-50117': ['reward1', 'dynface', 'rest'],
 'sub-50183': ['reward1', 'reward2', 'rest'],
 'sub-50111': ['reward1', 'reward2', 'efnback1', 'rest'],
 'sub-50018': ['reward1', 'efnback2'],
 'sub-50122': ['reward1', 'efnback2', 'rest'],
 'sub-50080': ['reward1'],
 'sub-50581': ['reward1', 'reward2', 'dynface', 'rest'],
 'sub-50127': ['reward1', 'reward2'],
 'sub-50167': ['reward